# Pràctica 4

In [112]:
from datasets import load_dataset

dataset = load_dataset("projecte-aina/catalan_general_crawling")

c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\datasets\load.py:1486: FutureWarning: The repository for projecte-aina/catalan_general_crawling contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/projecte-aina/catalan_general_crawling
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


In [1]:
dataset = dataset['train']

# i want to see the first 10 examples
for i in range(10):
    print(dataset[i])
    print()

NameError: name 'dataset' is not defined

Obtenim diferents mides de datasets

In [114]:
# i want to get the first 100 MB of the dataset
size = 0
for i in range(len(dataset)):
    size += len(dataset[i]['text'])
    if size > 100000000:
        print(i)
        break

dataset_100MB = dataset.select(list(range(i)))


# i want to get the first 500 MB of the dataset
size = 0
for j in range(len(dataset)):
    size += len(dataset[i]['text'])
    if size > 500000000:
        print(j)
        break

dataset_500MB = dataset.select(list(range(j)))


# i want to get the first 1 GB of the dataset
size = 0
for g in range(len(dataset)):
    size += len(dataset[i]['text'])
    if size > 1000000000:
        print(g)
        break

dataset_1GB = dataset.select(list(range(g)))

57333
369003
738007


## Preprocessament

In [115]:
import gensim
from gensim.models import Word2Vec
import re

# Funció per netejar i tokenitzar el text
def preprocess_text(text):
    # Neteja el text: treu caràcters no desitjats, converteix a minúscules, etc.
    text = re.sub(r'\W+', ' ', text)  # Substitueix caràcters no alfanumèrics per espais
    text = text.lower()  # Converteix a minúscules
    words = text.split()  # Tokenitza
    return words

# Carrega el fitxer de text i processa'l
corpus_100MB = []
for line in dataset_100MB:
    words = preprocess_text(line['text'])
    if words:  # Assegura't que la línia no està buida
        corpus_100MB.append(words)

# Comprova algunes línies per assegurar-te que tot està bé
print(corpus_100MB[:2])


[['reduïu', 'els', 'costos', 'dels', 'processos', 'administratius', 'al', 'vostre', 'organisme', 'públic', 'eviteu', 'els', 'desplaçaments', 'i', 'pèrdua', 'de', 'temps', 'als', 'ciutadans', 'en', 'les', 'seves', 'gestions', 'oferiu', 'una', 'administració', 'més', 'transparent', 'a', 'ciutadans', 'i', 'empreses', 'ens', 'grans', 'i', 'petits', 'experimenten', 'aquesta', 'transformació', 'amb', 'èxit', 'gràcies', 'al', 'suport', 'de', 'l', 'aoc', 'departament', 'de', 'sistemes', 'd', 'informació', 'i', 'processos', 'via', 'oberta', 'ens', 'ha', 'permès', 'fer', 'efectiu', 'el', 'dret', 'dels', 'ciutadans', 'a', 'no', 'aportar', 'documents', 'eliminant', 'paper', 'i', 'simplificant', 'procediments', 'e', 'fact', 'proporciona', 'informació', 'indispensable', 'per', 'a', 'la', 'realització', 'de', 'les', 'auditories', 'del', 'registre', 'comptable', 'de', 'factures', 'de', 'les', 'administracions', 'públiques', 'catalanes', 'coordinador', 'del', 'departament', 'd', 'informàtica', 'el', 's

## Entrenament model de similitud de Text Semàntic

In [116]:
from datasets import load_dataset

text_semantic = load_dataset("projecte-aina/sts-ca")

c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\datasets\load.py:1486: FutureWarning: The repository for projecte-aina/sts-ca contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/projecte-aina/sts-ca
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


In [117]:
from gensim.models import word2vec
model_100MB = word2vec.Word2Vec(corpus_100MB, vector_size=100, window=5, min_count=10, workers=4, epochs=25)
model_100MB.save("model_100MB")
# Obtenir un word-vector

In [118]:
model_100MB = Word2Vec.load("model_100MB")

In [119]:
# Exemple: trobar paraules similars
similar_words = model_100MB.wv.most_similar('paraula')
print(similar_words)

[('frase', 0.745411217212677), ('lletra', 0.6357048749923706), ('grafia', 0.6337482333183289), ('pronúncia', 0.5842017531394958), ('recomanació', 0.5701715350151062), ('locució', 0.5660364627838135), ('mania', 0.5606160759925842), ('piulada', 0.5556568503379822), ('cançó', 0.5542395114898682), ('versió', 0.5540514588356018)]


In [120]:
text_semantic_train = text_semantic['train']

In [121]:
text_semantic_test = text_semantic['test']

In [122]:
text_semantic_train[0]

{'sentence1': 'Atorga per primer cop les mencions Encarna Sanahuja a la inclusió de la perspectiva de gènere en docència Universitària',
 'sentence2': 'Creen la menció M. Encarna Sanahuja a la inclusió de la perspectiva de gènere en docència universitària',
 'label': 3.5}

In [123]:
# Preprcessament del text_semantic
corpus_semantic = []
semantic_score = []
for line in text_semantic_train:
    frase1 = preprocess_text(line['sentence1'])
    frase2 = preprocess_text(line['sentence2'])

    corpus_semantic.append((frase1, frase2))
    semantic_score.append(line['label'])

In [124]:
corpus_semantic_test = []
semantic_score_test = []
for line in text_semantic_test:
    frase1 = preprocess_text(line['sentence1'])
    frase2 = preprocess_text(line['sentence2'])

    corpus_semantic_test.append((frase1, frase2))
    semantic_score_test.append(line['label'])

In [125]:
vocabulari = {}

for frases in corpus_semantic:
    for frase in frases:
        for paraula in frase:
            if paraula in vocabulari:
                vocabulari[paraula] += 1
            else:
                vocabulari[paraula] = 1


In [126]:
vocabulari_reduit = {palabra for palabra, frecuencia in vocabulari.items() if frecuencia >= 10}


### Model Baseline

In [127]:
import tensorflow as tf

def build_and_compile_model(input_length: int = 100, hidden_size: int = 64, dictionary_size: int = 1000, embedding_size: int = 16) -> tf.keras.Model:
    
    input_1, input_2 = tf.keras.Input((input_length, ), dtype=tf.int32), tf.keras.Input((input_length, ), dtype=tf.int32)
    
    # Define Layers
    embedding = tf.keras.layers.Embedding(
        dictionary_size, embedding_size, input_length=input_length, mask_zero=True)
    
    lstm = tf.keras.layers.LSTM(hidden_size)
    
    concatenate = tf.keras.layers.Concatenate(axis=-1)
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')
    output = tf.keras.layers.Dense(1)
    
    # Pass through the layers
    _embedded_1, _embedded_2 = embedding(input_1), embedding(input_2)
    _lstm_1, _lstm_2 = lstm(_embedded_1), lstm(_embedded_2)
    
    _concatenated = concatenate([_lstm_1, _lstm_2])
    _hidden_output = hidden(_concatenated)
    _output = output(_hidden_output)
    
    # Define the model
    model = tf.keras.Model(inputs=(input_1, input_2), outputs=_output)
    model.compile(loss='mean_absolute_error',
                  optimizer=tf.keras.optimizers.Adam(0.01))
    return model

# Exemple d'ús del model
baseline_model = build_and_compile_model()
baseline_model.summary()

c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "functional_9"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_8       │ (None, 100)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_9       │ (None, 100)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_4         │ (None, 100, 16)   │     16,000 │ input_layer_8[0]… │
│ (Embedding)         │                   │            │ input_layer_9[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_8         │ (None, 100)       │          0 │ input_layer_8[0]… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_9         │ (None, 100)       │          0 │ input_layer_9[0]… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_4 (LSTM)       │ (None, 64)        │     20,736 │ embedding_4[0][0… │
│                     │                   │            │ not_equal_8[0][0… │
│                     │                   │            │ embedding_4[1][0… │
│                     │                   │            │ not_equal_9[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_7       │ (None, 128)       │          0 │ lstm_4[0][0],     │
│ (Concatenate)       │                   │            │ lstm_4[1][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_14 (Dense)    │ (None, 64)        │      8,256 │ concatenate_7[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_15 (Dense)    │ (None, 1)         │         65 │ dense_14[0][0]    │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 45,057 (176.00 KB)

 Trainable params: 45,057 (176.00 KB)

 Non-trainable params: 0 (0.00 B)

### 1. One-Hot

In [128]:
import tensorflow as tf

def build_and_compile_model(input_length: int = 764, hidden_size: int = 64, dictionary_size: int = 1000, embedding_size: int = 16) -> tf.keras.Model:
    
    input_1, input_2 = tf.keras.Input((input_length, ), dtype=tf.int32), tf.keras.Input((input_length, ), dtype=tf.int32)
    
    # Define Layers
    embedding = tf.keras.layers.Embedding(
        dictionary_size, embedding_size, input_length=input_length, mask_zero=True)
    
    lstm = tf.keras.layers.LSTM(hidden_size)
    
    concatenate = tf.keras.layers.Concatenate(axis=-1)
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')
    output = tf.keras.layers.Dense(1)
    
    # Pass through the layers
    _embedded_1, _embedded_2 = embedding(input_1), embedding(input_2)
    _lstm_1, _lstm_2 = lstm(_embedded_1), lstm(_embedded_2)
    
    _concatenated = concatenate([_lstm_1, _lstm_2])
    _hidden_output = hidden(_concatenated)
    _output = output(_hidden_output)
    
    # Define the model
    model = tf.keras.Model(inputs=(input_1, input_2), outputs=_output)
    model.compile(loss='mean_absolute_error',
                  optimizer=tf.keras.optimizers.Adam(0.01))
    return model

# Exemple d'ús del model
baseline_model = build_and_compile_model()
baseline_model.summary()

Model: "functional_11"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_10      │ (None, 764)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_11      │ (None, 764)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_5         │ (None, 764, 16)   │     16,000 │ input_layer_10[0… │
│ (Embedding)         │                   │            │ input_layer_11[0… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_10        │ (None, 764)       │          0 │ input_layer_10[0… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_11        │ (None, 764)       │          0 │ input_layer_11[0… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_5 (LSTM)       │ (None, 64)        │     20,736 │ embedding_5[0][0… │
│                     │                   │            │ not_equal_10[0][… │
│                     │                   │            │ embedding_5[1][0… │
│                     │                   │            │ not_equal_11[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_8       │ (None, 128)       │          0 │ lstm_5[0][0],     │
│ (Concatenate)       │                   │            │ lstm_5[1][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_16 (Dense)    │ (None, 64)        │      8,256 │ concatenate_8[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_17 (Dense)    │ (None, 1)         │         65 │ dense_16[0][0]    │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 45,057 (176.00 KB)

 Trainable params: 45,057 (176.00 KB)

 Non-trainable params: 0 (0.00 B)

In [129]:
import tensorflow as tf
def build_and_compile_model(hidden_size: int = 64) -> tf.keras.Model:
  model = tf.keras.Sequential([
      tf.keras.layers.Concatenate(axis=-1, ),
      tf.keras.layers.Dense(hidden_size, activation='relu'),
      tf.keras.layers.Dense(1)
  ])
  model.compile(loss='mean_absolute_error',
                optimizer=tf.keras.optimizers.Adam(0.001))
  return model

# Exemple d'ús del model
baseline_model = build_and_compile_model()
baseline_model.summary()

Model: "sequential_3"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ concatenate_9 (Concatenate)     │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_18 (Dense)                │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_19 (Dense)                │ ?                      │   0 (unbuilt) │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 0 (0.00 B)

In [130]:
import numpy as np

# Función para calcular la representación one-hot de un texto
def compute_one_hot_encoding(text, vocabulari):
    """
    Genera la representación one-hot de un texto utilizando un vocabulario predefinido.
    """
    one_hot_vector = np.zeros(len(vocabulari))
    vocabulario_list = list(vocabulari)
    for palabra in text:
        if palabra in vocabulari:
            index = vocabulario_list.index(palabra)
            one_hot_vector[index] = 1
        
    return one_hot_vector


In [131]:
# Passar les frases de corpus_semantic a vectors
one_hot_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(one_hot_corpus_semantic):
    one_hot_corpus_semantic[i] = (compute_one_hot_encoding(frase1, vocabulari_reduit), 
                                    compute_one_hot_encoding(frase2, vocabulari_reduit))

In [132]:
#### Entrenament de la xarxa amb els vectors de les frases ####

# Convertir les llistes de tuples a arrays de NumPy
vectors_1 = np.array([pair[0] for pair in one_hot_corpus_semantic])
vectors_2 = np.array([pair[1] for pair in one_hot_corpus_semantic])

# Comprovar si hi ha valors fora de rang i substituir-los
vectors_1 = np.clip(vectors_1, 0, 1)
vectors_2 = np.clip(vectors_2, 0, 1)

# Convertir les llistes de similituds a un array de NumPy
semantic_score = np.array(semantic_score)

baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)

Epoch 1/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 2s 9ms/step - loss: 1.7921 - val_loss: 0.8050
Epoch 2/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - loss: 0.8043 - val_loss: 0.7559
Epoch 3/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - loss: 0.6897 - val_loss: 0.7436
Epoch 4/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - loss: 0.6450 - val_loss: 0.7399
Epoch 5/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - loss: 0.5987 - val_loss: 0.7349
Epoch 6/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - loss: 0.5197 - val_loss: 0.7378
Epoch 7/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - loss: 0.4780 - val_loss: 0.7409
Epoch 8/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - loss: 0.4413 - val_loss: 0.7385
Epoch 9/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - loss: 0.3979 - val_loss: 0.7338
Epoch 10/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - loss: 0.3917 - val_loss: 0.7421
Epoch 11/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - loss: 0.3558 - val_loss: 0.7441
Epoch 12/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - loss: 0.3461 - v

In [133]:
from sklearn.metrics import mean_squared_error, r2_score

# Pasar las frases de corpus_semantic a vectores
one_hot_corpus_semantic_test = corpus_semantic_test.copy()
for i, (frase1, frase2) in enumerate(one_hot_corpus_semantic_test):
    one_hot_corpus_semantic_test[i] = (compute_one_hot_encoding(frase1, vocabulari_reduit), 
                                    compute_one_hot_encoding(frase2, vocabulari_reduit))

vectors_1 = np.array([pair[0] for pair in one_hot_corpus_semantic_test])
vectors_2 = np.array([pair[1] for pair in one_hot_corpus_semantic_test])

# Obtener predicciones del modelo
predicciones = baseline_model.predict([vectors_1, vectors_2])

# Calcular el error cuadrático medio (MSE)
mse = mean_squared_error(semantic_score_test, predicciones)

# Calcular el coeficiente de determinación (R^2)
r2 = r2_score(semantic_score_test, predicciones)

# Mostrar las predicciones, el MSE y el R^2
#print("Predicciones:", predicciones)
print("Error cuadrático medio (MSE):", mse)
print("Coeficiente de determinación (R^2):", r2)


16/16 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step
Error cuadrático medio (MSE): 1.0731909870927394
Coeficiente de determinación (R^2): -0.4214271306991577


### 2. Models Word2Vec pre-entrenats

In [134]:
import tensorflow as tf

def build_and_compile_model(input_length: int = 100, hidden_size: int = 64, dictionary_size: int = 1000, embedding_size: int = 16) -> tf.keras.Model:
    
    input_1, input_2 = tf.keras.Input((input_length, ), dtype=tf.int32), tf.keras.Input((input_length, ), dtype=tf.int32)
    
    # Define Layers
    embedding = tf.keras.layers.Embedding(
        dictionary_size, embedding_size, input_length=input_length, mask_zero=True)
    
    lstm = tf.keras.layers.LSTM(hidden_size)
    
    concatenate = tf.keras.layers.Concatenate(axis=-1)
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')
    output = tf.keras.layers.Dense(1)
    
    # Pass through the layers
    _embedded_1, _embedded_2 = embedding(input_1), embedding(input_2)
    _lstm_1, _lstm_2 = lstm(_embedded_1), lstm(_embedded_2)
    
    _concatenated = concatenate([_lstm_1, _lstm_2])
    _hidden_output = hidden(_concatenated)
    _output = output(_hidden_output)
    
    # Define the model
    model = tf.keras.Model(inputs=(input_1, input_2), outputs=_output)
    model.compile(loss='mean_absolute_error',
                  optimizer=tf.keras.optimizers.Adam(0.01))
    return model

# Exemple d'ús del model
baseline_model = build_and_compile_model()
baseline_model.summary()

c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\layers\core\embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "functional_13"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_12      │ (None, 100)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_13      │ (None, 100)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_6         │ (None, 100, 16)   │     16,000 │ input_layer_12[0… │
│ (Embedding)         │                   │            │ input_layer_13[0… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_12        │ (None, 100)       │          0 │ input_layer_12[0… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal_13        │ (None, 100)       │          0 │ input_layer_13[0… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_6 (LSTM)       │ (None, 64)        │     20,736 │ embedding_6[0][0… │
│                     │                   │            │ not_equal_12[0][… │
│                     │                   │            │ embedding_6[1][0… │
│                     │                   │            │ not_equal_13[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_10      │ (None, 128)       │          0 │ lstm_6[0][0],     │
│ (Concatenate)       │                   │            │ lstm_6[1][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_20 (Dense)    │ (None, 64)        │      8,256 │ concatenate_10[0… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_21 (Dense)    │ (None, 1)         │         65 │ dense_20[0][0]    │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 45,057 (176.00 KB)

 Trainable params: 45,057 (176.00 KB)

 Non-trainable params: 0 (0.00 B)

In [135]:
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer

# Word2Vec + Mean 
def compute_mean_embedding(text, model, embedding_dim):
    """
    Agafa els vectors d'embeddings de cada paraula en una frase o document i 
    calcula la mitjana dels vectors per obtenir una única representació vectorial 
    per a la frase o document.
    """
    vectors = [model[word] for word in text if word in model]
    if vectors:
        mean_vector = np.mean(vectors, axis=0)
    else:
        mean_vector = np.zeros(embedding_dim)
    return mean_vector


# Word2Vec + Mean Ponderada
def compute_weighted_mean_embedding(text, model, word2tfidf, embedding_dim):
    """
    Utilitza una ponderació per a cada vector de paraula, com ara la freqüència 
    inversa del document (TF-IDF), per calcular una mitjana ponderada dels vectors.
    """
    vectors = [model[word] * word2tfidf[word] for word in text if word in model and word in word2tfidf]
    if vectors:
        weighted_mean_vector = np.mean(vectors, axis=0)
    else:
        weighted_mean_vector = np.zeros(embedding_dim)
    return weighted_mean_vector

In [136]:
# Passar les frases de corpus_semantic a vectors
mean_embbeding_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(mean_embbeding_corpus_semantic):
    mean_embbeding_corpus_semantic[i] = (compute_mean_embedding(frase1, model_100MB.wv, 100), 
                                        compute_mean_embedding(frase2, model_100MB.wv, 100))

In [137]:
#### Entrenament de la xarxa amb els vectors de les frases ####

# Convertir les llistes de tuples a arrays de NumPy
vectors_1 = np.array([pair[0] for pair in mean_embbeding_corpus_semantic])
vectors_2 = np.array([pair[1] for pair in mean_embbeding_corpus_semantic])

# Comprovar si hi ha valors fora de rang i substituir-los
vectors_1 = np.clip(vectors_1, 0, 999)
vectors_2 = np.clip(vectors_2, 0, 999)

# Convertir les llistes de similituds a un array de NumPy
semantic_score = np.array(semantic_score)

print(vectors_1.shape)
print(vectors_2.shape)
print(semantic_score.shape)

baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)

(2073, 100)
(2073, 100)
(2073,)
Epoch 1/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 16s 105ms/step - loss: 1.0635 - val_loss: 0.6311
Epoch 2/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 5s 87ms/step - loss: 0.6793 - val_loss: 0.6458
Epoch 3/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 8s 161ms/step - loss: 0.6788 - val_loss: 0.6243
Epoch 4/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 10s 197ms/step - loss: 0.6664 - val_loss: 0.6242
Epoch 5/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 8s 158ms/step - loss: 0.6699 - val_loss: 0.6470
Epoch 6/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 7s 138ms/step - loss: 0.6870 - val_loss: 0.6501
Epoch 7/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 10s 119ms/step - loss: 0.7020 - val_loss: 0.6745
Epoch 8/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 5s 100ms/step - loss: 0.6755 - val_loss: 0.6458
Epoch 9/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 5s 93ms/step - loss: 0.6896 - val_loss: 0.6208
Epoch 10/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 5s 97ms/step - loss: 0.6797 - val_loss: 0.6208
Epoch 11/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 5s 92ms/step - loss: 0.6564 - val_loss: 0.6750
Epoch 12/50
52/52 ━━━

In [138]:
from sklearn.metrics import mean_squared_error, r2_score

# Pasar las frases de corpus_semantic a vectores
mean_embbeding_corpus_semantic_test = corpus_semantic_test.copy()
for i, (frase1, frase2) in enumerate(mean_embbeding_corpus_semantic_test):
    mean_embbeding_corpus_semantic_test[i] = (
        compute_mean_embedding(frase1, model_100MB.wv, 100),
        compute_mean_embedding(frase2, model_100MB.wv, 100)
    )

vectors_1 = np.array([pair[0] for pair in mean_embbeding_corpus_semantic_test])
vectors_2 = np.array([pair[1] for pair in mean_embbeding_corpus_semantic_test])

# Obtener predicciones del modelo
predicciones = baseline_model.predict([vectors_1, vectors_2])

# Calcular el error cuadrático medio (MSE)
mse = mean_squared_error(semantic_score_test, predicciones)

# Calcular el coeficiente de determinación (R^2)
r2 = r2_score(semantic_score_test, predicciones)

# Mostrar las predicciones, el MSE y el R^2
#print("Predicciones:", predicciones)
print("Error cuadrático medio (MSE):", mse)
print("Coeficiente de determinación (R^2):", r2)


16/16 ━━━━━━━━━━━━━━━━━━━━ 3s 79ms/step
Error cuadrático medio (MSE): 0.7906548506830702
Coeficiente de determinación (R^2): -0.04721176624298096


### 3. spaCy

In [139]:
!py -m spacy download ca_core_news_md

     ---------------------------------------- 0.0/49.2 MB ? eta -:--:--
     ---------------------------------------- 0.0/49.2 MB ? eta -:--:--
     ---------------------------------------- 0.0/49.2 MB ? eta -:--:--
     ---------------------------------------- 0.0/49.2 MB ? eta -:--:--
     ---------------------------------------- 0.0/49.2 MB ? eta -:--:--
     ---------------------------------------- 0.0/49.2 MB ? eta -:--:--
     --------------------------------------- 0.1/49.2 MB 192.5 kB/s eta 0:04:16
     --------------------------------------- 0.1/49.2 MB 192.5 kB/s eta 0:04:16
     --------------------------------------- 0.1/49.2 MB 151.0 kB/s eta 0:05:26
     --------------------------------------- 0.1/49.2 MB 151.0 kB/s eta 0:05:26
     --------------------------------------- 0.1/49.2 MB 151.0 kB/s eta 0:05:26
     --------------------------------------- 0.1/49.2 MB 159.4 kB/s eta 0:05:09
     --------------------------------------- 0.1/49.2 MB 159.4 kB/s eta 0:05:09
     ---

C:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\transformers\utils\generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


     ------------------------ ------------- 31.5/49.2 MB 166.2 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 166.2 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 166.2 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 166.2 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 166.2 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 166.2 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 165.7 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 165.7 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 165.2 kB/s eta 0:01:48
     ------------------------ ------------- 31.5/49.2 MB 165.5 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 165.5 kB/s eta 0:01:47
     ------------------------ ------------- 31.5/49.2 MB 165.5 kB/s eta 0:01:47
     ------------------------ ----------

In [140]:
import tensorflow as tf
import numpy as np

def build_and_compile_model(input_size: int, hidden_size: int = 64) -> tf.keras.Model:
    input_1 = tf.keras.layers.Input(shape=(input_size,))
    input_2 = tf.keras.layers.Input(shape=(input_size,))
    
    concatenated = tf.keras.layers.Concatenate(axis=-1)([input_1, input_2])
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')(concatenated)
    output = tf.keras.layers.Dense(1)(hidden)
    
    model = tf.keras.Model(inputs=[input_1, input_2], outputs=output)
    
    model.compile(loss='mean_absolute_error',
                  optimizer=tf.keras.optimizers.Adam(0.001))
    return model


In [141]:
import spacy

nlp_md = spacy.load('ca_core_news_md')

In [142]:
def spacy_mean_embedding(text1, text2, model):
    """
    Agafa els vectors d'embeddings de cada paraula en una frase o document i 
    calcula la mitjana dels vectors per obtenir una única representació vectorial 
    per a la frase o document.
    """
    text1 = ' '.join(text1)
    text2 = ' '.join(text2)
    frase1 = model(text1).vector
    frase2 = model(text2).vector
    
    return frase1, frase2

In [143]:
# Passar les frases de corpus_semantic a vectors
spacy_mean_embbeding_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(spacy_mean_embbeding_corpus_semantic):
    
    frase1, frase2 = spacy_mean_embedding(frase1, frase2, nlp_md)
    spacy_mean_embbeding_corpus_semantic[i] = (frase1, frase2)

In [144]:
#### Entrenament de la xarxa amb els vectors de les frases ####

# Convertir les llistes de tuples a arrays de NumPy
vectors_1 = np.array([pair[0] for pair in spacy_mean_embbeding_corpus_semantic])
vectors_2 = np.array([pair[1] for pair in spacy_mean_embbeding_corpus_semantic])

# Comprovar si hi ha valors fora de rang i substituir-los
#vectors_1 = np.clip(vectors_1, 0, 999)
#vectors_2 = np.clip(vectors_2, 0, 999)

# Convertir les llistes de similituds a un array de NumPy
semantic_score = np.array(semantic_score)

print(vectors_1.shape)
print(vectors_2.shape)
print(semantic_score.shape)

baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)

(2073, 300)
(2073, 300)
(2073,)
Epoch 1/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 20s 260ms/step - loss: 0.7000 - val_loss: 0.6276
Epoch 2/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 12s 230ms/step - loss: 0.6557 - val_loss: 0.6276
Epoch 3/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 12s 229ms/step - loss: 0.6760 - val_loss: 0.6240
Epoch 4/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 12s 232ms/step - loss: 0.6643 - val_loss: 0.6265
Epoch 5/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 12s 228ms/step - loss: 0.6688 - val_loss: 0.6361
Epoch 6/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 21s 403ms/step - loss: 0.6633 - val_loss: 0.6367
Epoch 7/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 39s 356ms/step - loss: 0.6573 - val_loss: 0.6410
Epoch 8/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 22s 375ms/step - loss: 0.6627 - val_loss: 0.6364
Epoch 9/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 24s 430ms/step - loss: 0.6645 - val_loss: 0.6731
Epoch 10/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 22s 422ms/step - loss: 0.6622 - val_loss: 0.6523
Epoch 11/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 44s 468ms/step - loss: 0.6342 - val_loss: 0.6492
Epoch 12/

In [145]:
from sklearn.metrics import mean_squared_error, r2_score

# Pasar las frases de corpus_semantic a vectores
spacy_mean_embbeding_corpus_semantic_test = corpus_semantic_test.copy()
for i, (frase1, frase2) in enumerate(spacy_mean_embbeding_corpus_semantic_test):
    
    frase1, frase2 = spacy_mean_embedding(frase1, frase2, nlp_md)
    spacy_mean_embbeding_corpus_semantic_test[i] = (frase1, frase2)

vectors_1 = np.array([pair[0] for pair in spacy_mean_embbeding_corpus_semantic_test])
vectors_2 = np.array([pair[1] for pair in spacy_mean_embbeding_corpus_semantic_test])

# Obtener predicciones del modelo
predicciones = baseline_model.predict([vectors_1, vectors_2])

# Calcular el error cuadrático medio (MSE)
mse = mean_squared_error(semantic_score_test, predicciones)

# Calcular el coeficiente de determinación (R^2)
r2 = r2_score(semantic_score_test, predicciones)

# Mostrar las predicciones, el MSE y el R^2
#print("Predicciones:", predicciones)
print("Error cuadrático medio (MSE):", mse)
print("Coeficiente de determinación (R^2):", r2)


16/16 ━━━━━━━━━━━━━━━━━━━━ 4s 112ms/step
Error cuadrático medio (MSE): 0.8124522844513281
Coeficiente de determinación (R^2): -0.07608211040496826


#### 4.RoBERTa

In [146]:
!py -m spacy download ca_core_news_trf

     ---------------------------------------- 0.0/457.1 MB ? eta -:--:--
     ---------------------------------------- 0.0/457.1 MB ? eta -:--:--
     ---------------------------------------- 0.0/457.1 MB ? eta -:--:--
     ---------------------------------------- 0.0/457.1 MB ? eta -:--:--
     -------------------------------------- 0.0/457.1 MB 667.8 kB/s eta 0:11:25
     -------------------------------------- 0.1/457.1 MB 491.5 kB/s eta 0:15:30
     -------------------------------------- 0.1/457.1 MB 491.5 kB/s eta 0:15:30
     -------------------------------------- 0.1/457.1 MB 491.5 kB/s eta 0:15:30
     -------------------------------------- 0.1/457.1 MB 491.5 kB/s eta 0:15:30
     -------------------------------------- 0.1/457.1 MB 268.7 kB/s eta 0:28:21
     -------------------------------------- 0.1/457.1 MB 277.4 kB/s eta 0:27:28
     -------------------------------------- 0.1/457.1 MB 262.6 kB/s eta 0:29:01
     -------------------------------------- 0.2/457.1 MB 262.6 kB/s 

C:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\transformers\utils\generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
ERROR: Exception:
Traceback (most recent call last):
  File "C:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\pip\_vendor\urllib3\response.py", line 438, in _error_catcher
    yield
  File "C:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\pip\_vendor\urllib3\response.py", line 561, in read
    data = self._fp_read(amt) if not fp_closed else b""
           ^^^^^^^^^^^^^^^^^^
  File "C:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\pip\_vendor\urllib3\response.py", line 527, in _fp_read
    return self._fp.read(amt) if amt is not None else self._fp.read()
           ^^^^^^^^^^^^^^^^^^
  File "C:\Users\USER\AppData\Local\Programs\Python\Python311\Li


      ------------------------------------ 11.7/457.1 MB 196.1 kB/s eta 0:37:51
      ------------------------------------ 11.7/457.1 MB 196.1 kB/s eta 0:37:51
      ------------------------------------ 11.7/457.1 MB 195.2 kB/s eta 0:38:02
      ------------------------------------ 11.7/457.1 MB 195.4 kB/s eta 0:37:59
      ------------------------------------ 11.8/457.1 MB 195.3 kB/s eta 0:38:00
      ------------------------------------ 11.8/457.1 MB 194.7 kB/s eta 0:38:08
      ------------------------------------ 11.8/457.1 MB 194.8 kB/s eta 0:38:07
      ------------------------------------ 11.8/457.1 MB 194.6 kB/s eta 0:38:09
      ------------------------------------ 11.8/457.1 MB 194.6 kB/s eta 0:38:09
      ------------------------------------ 11.8/457.1 MB 195.0 kB/s eta 0:38:04
      ------------------------------------ 11.8/457.1 MB 194.7 kB/s eta 0:38:08
      ------------------------------------ 11.9/457.1 MB 194.8 kB/s eta 0:38:07
      ---------------------------------

In [147]:
import spacy

nlp_trf = spacy.load('ca_core_news_trf')

In [155]:
def spacy_trf_CLS(frase1, frase2, model):# Procesar la frase
    frase1 = ' '.join(frase1)
    frase2 = ' '.join(frase2)
    doc1 = model(frase1)
    doc2 = model(frase2)

    # Obtener el embedding CLS
    embedding_CLS1 = doc1._.trf_data.last_hidden_layer_state
    embedding_array1 = embedding_CLS1.data
    embedding_CLS2 = doc2._.trf_data.last_hidden_layer_state
    embedding_array2 = embedding_CLS2.data
    
    return embedding_array1, embedding_array2


In [156]:
spacy_trf_CLS_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(spacy_trf_CLS_corpus_semantic):
    
    frase1, frase2 = spacy_trf_CLS(frase1, frase2, nlp_trf)
    spacy_trf_CLS_corpus_semantic[i] = (frase1, frase2)

In [169]:
#### Entrenament de la xarxa amb els vectors de les frases ####

# Convertir les llistes de tuples a arrays de NumPy
vectors_1 = np.array([pair[0][0] for pair in spacy_trf_CLS_corpus_semantic])
vectors_2 = np.array([pair[0][1] for pair in spacy_trf_CLS_corpus_semantic])

# Comprovar si hi ha valors fora de rang i substituir-los
#vectors_1 = np.clip(vectors_1, 0, 999)
#vectors_2 = np.clip(vectors_2, 0, 999)

# Convertir les llistes de similituds a un array de NumPy
semantic_score = np.array(semantic_score)

print(vectors_1.shape)
print(vectors_2.shape)
print(semantic_score.shape)

baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)

(2073, 768)
(2073, 768)
(2073,)
Epoch 1/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 46s 882ms/step - loss: 0.6666 - val_loss: 0.6327
Epoch 2/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 35s 675ms/step - loss: 0.6747 - val_loss: 0.6406
Epoch 3/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 41s 669ms/step - loss: 0.6739 - val_loss: 0.6379
Epoch 4/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 35s 670ms/step - loss: 0.6575 - val_loss: 0.6697
Epoch 5/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 41s 666ms/step - loss: 0.6988 - val_loss: 0.6355
Epoch 6/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 36s 698ms/step - loss: 0.6612 - val_loss: 0.6397
Epoch 7/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 39s 662ms/step - loss: 0.6655 - val_loss: 0.6523
Epoch 8/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 34s 663ms/step - loss: 0.6511 - val_loss: 0.6542
Epoch 9/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 34s 663ms/step - loss: 0.6820 - val_loss: 0.6452
Epoch 10/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 35s 666ms/step - loss: 0.6817 - val_loss: 0.6422
Epoch 11/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 41s 662ms/step - loss: 0.6575 - val_loss: 0.6369
Epoch 12/

In [172]:
from sklearn.metrics import mean_squared_error, r2_score

# Pasar las frases de corpus_semantic a vectores
spacy_trf_CLS_corpus_semantic_test = corpus_semantic_test.copy()
for i, (frase1, frase2) in enumerate(spacy_trf_CLS_corpus_semantic_test):
    
    frase1, frase2 = spacy_trf_CLS(frase1, frase2, nlp_trf)
    spacy_trf_CLS_corpus_semantic_test[i] = (frase1, frase2)

vectors_1 = np.array([pair[0][0] for pair in spacy_trf_CLS_corpus_semantic_test])
vectors_2 = np.array([pair[0][1] for pair in spacy_trf_CLS_corpus_semantic_test])

# Obtener predicciones del modelo
predicciones = baseline_model.predict([vectors_1, vectors_2])

# Calcular el error cuadrático medio (MSE)
mse = mean_squared_error(semantic_score_test, predicciones)

# Calcular el coeficiente de determinación (R^2)
r2 = r2_score(semantic_score_test, predicciones)

# Mostrar las predicciones, el MSE y el R^2
#print("Predicciones:", predicciones)
print("Error cuadrático medio (MSE):", mse)
print("Coeficiente de determinación (R^2):", r2)


16/16 ━━━━━━━━━━━━━━━━━━━━ 3s 188ms/step
Error cuadrático medio (MSE): 0.857102274135646
Coeficiente de determinación (R^2): -0.13522052764892578


In [176]:
import spacy
import numpy as np

# Cargar el modelo
nlp_trf = spacy.load('ca_core_news_trf')

# Frase de ejemplo
frase1 = 'atorga per primer cop les mencions encarna sanahuja a la inclusió de la perspectiva de gènere en docència universitària'
doc = nlp_trf(frase1)

# Obtener las representaciones de la última capa oculta
embeddings = doc._.trf_data.last_hidden_layer_state

# Convertir a numpy array
embeddings_np = np.array(embeddings.data)

# Calcular la media de los embeddings a lo largo del eje de las palabras
mean_embedding = np.mean(embeddings_np, axis=1)

print(mean_embedding)


[-0.02514403 -0.02423467 -0.02222145 -0.02104405 -0.0206563  -0.02282859
 -0.02231251 -0.01975315 -0.01896309 -0.01849412 -0.01996193 -0.02303372
 -0.02044051 -0.02010201 -0.02229198 -0.02012951 -0.02090405 -0.01915449
 -0.02045573 -0.02013825 -0.02128188]


In [177]:
def spacy_trf_mean(frase1, frase2, model):
    frase1 = ' '.join(frase1)
    frase2 = ' '.join(frase2)
    doc1 = model(frase1)
    doc2 = model(frase2)

    # Obtener el embedding CLS
    embedding_CLS1 = doc1._.trf_data.last_hidden_layer_state
    embedding_array1 = embedding_CLS1.data
    embedding_CLS2 = doc2._.trf_data.last_hidden_layer_state
    embedding_array2 = embedding_CLS2.data
    
    return np.array(embedding_array1.data), np.array(embedding_array2.data)

In [178]:
spacy_trf_mean_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(spacy_trf_mean_corpus_semantic):
    
    frase1, frase2 = spacy_trf_CLS(frase1, frase2, nlp_trf)
    spacy_trf_mean_corpus_semantic[i] = (frase1, frase2)

In [183]:
#### Entrenament de la xarxa amb els vectors de les frases ####

# Convertir les llistes de tuples a arrays de NumPy
vectors_1 = np.array([pair[0][0] for pair in spacy_trf_CLS_corpus_semantic])
vectors_2 = np.array([pair[0][1] for pair in spacy_trf_CLS_corpus_semantic])

# Comprovar si hi ha valors fora de rang i substituir-los
#vectors_1 = np.clip(vectors_1, 0, 999)
#vectors_2 = np.clip(vectors_2, 0, 999)

# Convertir les llistes de similituds a un array de NumPy
semantic_score = np.array(semantic_score)

print(vectors_1.shape)
print(vectors_2.shape)
print(semantic_score.shape)

baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)

(2073, 768)
(2073, 768)
(2073,)
Epoch 1/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 38s 729ms/step - loss: 0.6008 - val_loss: 0.6551
Epoch 2/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 31s 533ms/step - loss: 0.5929 - val_loss: 0.6602
Epoch 3/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 28s 538ms/step - loss: 0.5979 - val_loss: 0.6682
Epoch 4/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 27s 519ms/step - loss: 0.6061 - val_loss: 0.6872
Epoch 5/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 27s 522ms/step - loss: 0.5853 - val_loss: 0.6781
Epoch 6/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 27s 518ms/step - loss: 0.6001 - val_loss: 0.6741
Epoch 7/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 27s 521ms/step - loss: 0.5674 - val_loss: 0.6826
Epoch 8/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 27s 522ms/step - loss: 0.5815 - val_loss: 0.6671
Epoch 9/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 28s 536ms/step - loss: 0.5939 - val_loss: 0.6697
Epoch 10/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 28s 533ms/step - loss: 0.5774 - val_loss: 0.6673
Epoch 11/50
52/52 ━━━━━━━━━━━━━━━━━━━━ 27s 528ms/step - loss: 0.5625 - val_loss: 0.6827
Epoch 12/

In [184]:
from sklearn.metrics import mean_squared_error, r2_score

# Pasar las frases de corpus_semantic a vectores
spacy_trf_mean_corpus_semantic_test = corpus_semantic_test.copy()
for i, (frase1, frase2) in enumerate(spacy_trf_mean_corpus_semantic_test):
    
    frase1, frase2 = spacy_trf_mean(frase1, frase2, nlp_trf)
    spacy_trf_mean_corpus_semantic_test[i] = (frase1, frase2)

vectors_1 = np.array([pair[0][0] for pair in spacy_trf_mean_corpus_semantic_test])
vectors_2 = np.array([pair[0][1] for pair in spacy_trf_mean_corpus_semantic_test])

# Obtener predicciones del modelo
predicciones = baseline_model.predict([vectors_1, vectors_2])

# Calcular el error cuadrático medio (MSE)
mse = mean_squared_error(semantic_score_test, predicciones)

# Calcular el coeficiente de determinación (R^2)
r2 = r2_score(semantic_score_test, predicciones)

# Mostrar las predicciones, el MSE y el R^2
#print("Predicciones:", predicciones)
print("Error cuadrático medio (MSE):", mse)
print("Coeficiente de determinación (R^2):", r2)


16/16 ━━━━━━━━━━━━━━━━━━━━ 3s 160ms/step
Error cuadrático medio (MSE): 0.9494762308904419
Coeficiente de determinación (R^2): -0.25756847858428955


### 5. RoBERTa fine-tuned

In [185]:
from transformers import pipeline, AutoTokenizer
from scipy.special import logit

model = 'projecte-aina/roberta-base-ca-v2-cased-sts'
tokenizer = AutoTokenizer.from_pretrained(model)
pipe = pipeline('text-classification', model=model, tokenizer=tokenizer)

c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [188]:
from transformers import AutoTokenizer, AutoModel
import torch

model_name = 'projecte-aina/roberta-base-ca-v2-cased-sts'
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)


c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of RobertaModel were not initialized from the model checkpoint at projecte-aina/roberta-base-ca-v2-cased-sts and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [189]:
def get_embeddings(text):
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True)
    with torch.no_grad():
        outputs = model(**inputs)
    return outputs.last_hidden_state

In [190]:
RoBERTa_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(RoBERTa_corpus_semantic):
    frase1 = get_embeddings(frase1)
    frase2 = get_embeddings(frase2)
    RoBERTa_corpus_semantic[i] = (frase1, frase2)

In [193]:
RoBERTa_corpus_semantic

[(tensor([[[ 0.1028, -0.2685,  0.3263,  ..., -0.0254, -0.1854,  0.0947],
           [ 0.1029, -0.2684,  0.3250,  ..., -0.0259, -0.1851,  0.0949],
           [ 0.1026, -0.2693,  0.3246,  ..., -0.0259, -0.1843,  0.0952],
           [ 0.1026, -0.2688,  0.3259,  ..., -0.0257, -0.1852,  0.0952],
           [ 0.1026, -0.2688,  0.3259,  ..., -0.0257, -0.1852,  0.0952]],
  
          [[ 0.1197, -0.2725,  0.3522,  ..., -0.0086, -0.1891,  0.0785],
           [ 0.1200, -0.2718,  0.3520,  ..., -0.0092, -0.1888,  0.0790],
           [ 0.1191, -0.2727,  0.3509,  ..., -0.0088, -0.1866,  0.0793],
           [ 0.1197, -0.2728,  0.3516,  ..., -0.0086, -0.1883,  0.0786],
           [ 0.1197, -0.2728,  0.3516,  ..., -0.0086, -0.1883,  0.0786]],
  
          [[ 0.1267, -0.2745,  0.3581,  ..., -0.0127, -0.1878,  0.0865],
           [ 0.1270, -0.2743,  0.3572,  ..., -0.0128, -0.1870,  0.0863],
           [ 0.1262, -0.2751,  0.3570,  ..., -0.0130, -0.1856,  0.0870],
           [ 0.1265, -0.2747,  0.3575,  ...

In [192]:
#### Entrenament de la xarxa amb els vectors de les frases ####

# Convertir les llistes de tuples a arrays de NumPy
vectors_1 = np.array([pair[0][0] for pair in RoBERTa_corpus_semantic])
vectors_2 = np.array([pair[0][1] for pair in RoBERTa_corpus_semantic])

# Comprovar si hi ha valors fora de rang i substituir-los
#vectors_1 = np.clip(vectors_1, 0, 999)
#vectors_2 = np.clip(vectors_2, 0, 999)

# Convertir les llistes de similituds a un array de NumPy
semantic_score = np.array(semantic_score)

print(vectors_1.shape)
print(vectors_2.shape)
print(semantic_score.shape)

baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)

ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (2073,) + inhomogeneous part.

In [ ]:
def prepare(sentence_pairs):
    sentence_pairs_prep = []
    for s1, s2 in sentence_pairs:
        sentence_pairs_prep.append(f"{tokenizer.cls_token} {s1}{tokenizer.sep_token}{tokenizer.sep_token} {s2}{tokenizer.sep_token}")
    return sentence_pairs_prep

In [ ]:
import numpy as np
import torch
from transformers import AutoTokenizer, AutoModel
model_name = 'projecte-aina/roberta-base-ca-v2-cased-sts'
tokenizer = AutoTokenizer.from_pretrained(model_name)
transformer_model = AutoModel.from_pretrained(model_name)

# Convert sentence pairs to embeddings using the transformer model
def get_embeddings(sentence_pairs):
    prepared_pairs = prepare(sentence_pairs)
    embeddings = []
    for pair in prepared_pairs:
        inputs = tokenizer(pair, return_tensors='pt', truncation=True, padding=True, max_length=512)
        with torch.no_grad():
            outputs = transformer_model(**inputs)
        embeddings.append(outputs.last_hidden_state.mean(dim=1).squeeze().numpy())
    return embeddings

fine_tuned_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(fine_tuned_corpus_semantic):
    fine_tuned_corpus_semantic[i] = (' '.join(frase1), ' '.join(frase2))

embeddings = get_embeddings(fine_tuned_corpus_semantic)

Some weights of RobertaModel were not initialized from the model checkpoint at projecte-aina/roberta-base-ca-v2-cased-sts and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


KeyboardInterrupt: 

In [ ]:


# Separate embeddings into two arrays for the sentence pairs
vectors_1 = np.array([embedding[:len(embedding)//2] for embedding in embeddings])
vectors_2 = np.array([embedding[len(embedding)//2:] for embedding in embeddings])

# Assuming 'semantic_score' is already defined as the target similarity scores
semantic_score = np.array(semantic_score)

print(vectors_1.shape)
print(vectors_2.shape)
print(semantic_score.shape)

# Define and compile the Keras model
def build_and_compile_model(input_length: int, hidden_size: int = 64) -> tf.keras.Model:
    input_1, input_2 = tf.keras.Input(shape=(input_length,)), tf.keras.Input(shape=(input_length,))
    
    dense = tf.keras.layers.Dense(hidden_size, activation='relu')
    concatenate = tf.keras.layers.Concatenate(axis=-1)
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')
    output = tf.keras.layers.Dense(1)
    
    _dense_1, _dense_2 = dense(input_1), dense(input_2)
    _concatenated = concatenate([_dense_1, _dense_2])
    _hidden_output = hidden(_concatenated)
    _output = output(_hidden_output)
    
    model = tf.keras.Model(inputs=(input_1, input_2), outputs=_output)
    model.compile(loss='mean_absolute_error', optimizer=tf.keras.optimizers.Adam(0.01))
    return model

input_length = vectors_1.shape[1]
baseline_model = build_and_compile_model(input_length)
baseline_model.summary()

# Train the model
baseline_model.fit(
    [vectors_1, vectors_2], 
    semantic_score, 
    epochs=50, 
    batch_size=32, 
    validation_split=0.2
)


c:\Users\USER\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of RobertaModel were not initialized from the model checkpoint at projecte-aina/roberta-base-ca-v2-cased-sts and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


KeyboardInterrupt: 

In [ ]:
fine_runed_corpus_semantic = corpus_semantic.copy()
for i, (frase1, frase2) in enumerate(fine_runed_corpus_semantic):
    frase1 = ' '.join(frase1)
    frase2 = ' '.join(frase2)
    fine_runed_corpus_semantic[i] = (frase1, frase2)


In [ ]:
predictions = pipe(prepare(fine_runed_corpus_semantic), add_special_tokens=False)

# convert back to scores to the original 0 and 5 interval
for prediction in predictions:
    prediction['score'] = logit(prediction['score'])
print(predictions)

[{'label': 'SIMILARITY', 'score': 3.639443974101274}, {'label': 'SIMILARITY', 'score': 1.3343049254405437}, {'label': 'SIMILARITY', 'score': 3.6255003414699982}, {'label': 'SIMILARITY', 'score': 2.8571212701413073}, {'label': 'SIMILARITY', 'score': 1.7412681993979517}, {'label': 'SIMILARITY', 'score': 2.902458331608203}, {'label': 'SIMILARITY', 'score': 3.3925175786892536}, {'label': 'SIMILARITY', 'score': 2.7214751443641485}, {'label': 'SIMILARITY', 'score': 2.848001481281147}, {'label': 'SIMILARITY', 'score': 2.8075600107730767}, {'label': 'SIMILARITY', 'score': 2.9737861311233997}, {'label': 'SIMILARITY', 'score': 0.946479625573919}, {'label': 'SIMILARITY', 'score': 2.0864164114103474}, {'label': 'SIMILARITY', 'score': 3.390759591752991}, {'label': 'SIMILARITY', 'score': 3.119538929859854}, {'label': 'SIMILARITY', 'score': 2.835003453924068}, {'label': 'SIMILARITY', 'score': 1.6847840009938235}, {'label': 'SIMILARITY', 'score': 3.1470772247192316}, {'label': 'SIMILARITY', 'score': 2

In [ ]:
from sklearn.metrics import mean_squared_error, r2_score

# Pasar las frases de corpus_semantic a vectores
mean_embbeding_corpus_semantic_test = corpus_semantic_test.copy()
for i, (frase1, frase2) in enumerate(mean_embbeding_corpus_semantic_test):
    mean_embbeding_corpus_semantic_test[i] = (
        compute_mean_embedding(frase1, model_100MB.wv, 100),
        compute_mean_embedding(frase2, model_100MB.wv, 100)
    )

vectors_1 = np.array([pair[0] for pair in mean_embbeding_corpus_semantic_test])
vectors_2 = np.array([pair[1] for pair in mean_embbeding_corpus_semantic_test])

# Obtener predicciones del modelo
predicciones = baseline_model.predict([vectors_1, vectors_2])

# Calcular el error cuadrático medio (MSE)
mse = mean_squared_error(semantic_score_test, predicciones)

# Calcular el coeficiente de determinación (R^2)
r2 = r2_score(semantic_score_test, predicciones)

# Mostrar las predicciones, el MSE y el R^2
#print("Predicciones:", predicciones)
print("Error cuadrático medio (MSE):", mse)
print("Coeficiente de determinación (R^2):", r2)


### model amb embeddings entrenables

#### Random Embeddings

In [ ]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from gensim.models import Word2Vec

vectors_1 =[pair[0] for pair in mean_embbeding_corpus_semantic]
vectors_2 =[pair[1] for pair in mean_embbeding_corpus_semantic]

# Tokenització i creació del vocabulari
tokenizer = Tokenizer()
tokenizer.fit_on_texts(texts_1 + texts_2)
sequences_1 = tokenizer.texts_to_sequences(texts_1)
sequences_2 = tokenizer.texts_to_sequences(texts_2)
word_index = tokenizer.word_index

# Padding de les seqüències
max_length = 10
data_1 = pad_sequences(sequences_1, maxlen=max_length)
data_2 = pad_sequences(sequences_2, maxlen=max_length)

# Paràmetres del model
vocab_size = len(word_index) + 1
embedding_dim = 100
hidden_size = 64
input_length = max_length

# Creació d'embeddings aleatoris
random_embeddings = np.random.uniform(-1, 1, (vocab_size, embedding_dim))

# Creació d'embeddings de Word2Vec
texts_combined = [text.split() for text in texts_1 + texts_2]
word2vec_model = Word2Vec(texts_combined, vector_size=embedding_dim, window=5, min_count=1, workers=4)
word2vec_embeddings = np.zeros((vocab_size, embedding_dim))
for word, i in word_index.items():
    if word in word2vec_model.wv:
        word2vec_embeddings[i] = word2vec_model.wv[word]

# Entrenament del model amb embeddings aleatoris
model_random = build_and_compile_model(random_embeddings, input_length=max_length, hidden_size=hidden_size)
model_random.fit([data_1, data_2], labels, epochs=10, batch_size=2)

# Entrenament del model amb embeddings de Word2Vec
model_word2vec = build_and_compile_model(word2vec_embeddings, input_length=max_length, hidden_size=hidden_size)
model_word2vec.fit([data_1, data_2], labels, epochs=10, batch_size=2)

# Avalua els resultats dels models
loss_random = model_random.evaluate([data_1, data_2], labels)
loss_word2vec = model_word2vec.evaluate([data_1, data_2], labels)

print(f'Random Embeddings - Loss: {loss_random}')
print(f'Word2Vec Embeddings - Loss: {loss_word2vec}')


In [ ]:
import tensorflow as tf
def build_and_compile_model(
        input_length: int = 10, hidden_size: int = 64, dictionary_size: int = 1000, embedding_size: int = 16,
) -> tf.keras.Model:
    input_1, input_2 = tf.keras.Input((input_length, ), dtype=tf.int32, ), tf.keras.Input((input_length, ), dtype=tf.int32, )
    # Define Layers
    embedding = tf.keras.layers.Embedding(
        dictionary_size, embedding_size, input_length=input_length, mask_zero=True, )
    pooling = tf.keras.layers.GlobalAveragePooling1D()
    concatenate = tf.keras.layers.Concatenate(axis=-1, )
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')
    output = tf.keras.layers.Dense(1)
    # Pass through the layers
    _input_mask_1, _input_mask_2 = tf.not_equal(input_1, 0), tf.not_equal(input_2, 0)
    _embedded_1, _embedded_2 = embedding(input_1, ), embedding(input_2, )
    _pooled_1, _pooled_2 = pooling(_embedded_1, mask=_input_mask_1), pooling(_embedded_2, mask=_input_mask_2)
    _concatenated = concatenate((_pooled_1, _pooled_2, ))
    _hidden_output = hidden(_concatenated)
    _output = output(_hidden_output)
    # Define the model
    model = tf.keras.Model(inputs=(input_1, input_2, ), outputs=_output, )
    model.compile(loss='mean_absolute_error',
                optimizer=tf.keras.optimizers.Adam(0.001))
    return model

#### Word2Vec

In [ ]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from gensim.models import Word2Vec

# Exemple de dades
texts_1 = ["aquest és un text d'exemple", "un altre text"]
texts_2 = ["aquest és un altre text", "un text diferent"]
labels = [0.8, 0.4]  # Similitud entre les frases

# Tokenització i creació del vocabulari
tokenizer = Tokenizer()
tokenizer.fit_on_texts(texts_1 + texts_2)
sequences_1 = tokenizer.texts_to_sequences(texts_1)
sequences_2 = tokenizer.texts_to_sequences(texts_2)
word_index = tokenizer.word_index

# Padding de les seqüències
max_length = 10
data_1 = pad_sequences(sequences_1, maxlen=max_length)
data_2 = pad_sequences(sequences_2, maxlen=max_length)

# Paràmetres del model
vocab_size = len(word_index) + 1
embedding_dim = 100
hidden_size = 64
input_length = max_length

# Creació d'embeddings de Word2Vec
texts_combined = [text.split() for text in texts_1 + texts_2]
word2vec_model = Word2Vec(texts_combined, vector_size=embedding_dim, window=5, min_count=1, workers=4)
word2vec_embeddings = np.zeros((vocab_size, embedding_dim))
for word, i in word_index.items():
    if word in word2vec_model.wv:
        word2vec_embeddings[i] = word2vec_model.wv[word]

def build_and_compile_model(embedding_matrix, input_length: int = 100, hidden_size: int = 64) -> tf.keras.Model:
    input_1, input_2 = tf.keras.Input((input_length, ), dtype=tf.int32), tf.keras.Input((input_length, ), dtype=tf.int32)

    # Define Layers
    embedding = tf.keras.layers.Embedding(
        vocab_size, embedding_dim, weights=[embedding_matrix], input_length=input_length, mask_zero=True, trainable=True)

    lstm = tf.keras.layers.LSTM(hidden_size)

    concatenate = tf.keras.layers.Concatenate(axis=-1)
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')
    output = tf.keras.layers.Dense(1)

    # Pass through the layers
    _embedded_1, _embedded_2 = embedding(input_1), embedding(input_2)
    _lstm_1, _lstm_2 = lstm(_embedded_1), lstm(_embedded_2)

    _concatenated = concatenate([_lstm_1, _lstm_2])
    _hidden_output = hidden(_concatenated)
    _output = output(_hidden_output)

    # Define the model
    model = tf.keras.Model(inputs=(input_1, input_2), outputs=_output)
    model.compile(loss='mean_absolute_error',
                  optimizer=tf.keras.optimizers.Adam(0.01))
    return model

# Entrenament del model amb embeddings de Word2Vec
model_word2vec = build_and_compile_model(word2vec_embeddings, input_length=max_length, hidden_size=hidden_size)
model_word2vec.fit([data_1, data_2], labels, epochs=10, batch_size=2)

# Avalua els resultats dels models
loss_word2vec = model_word2vec.evaluate([data_1, data_2], labels)

print(f'Word2Vec Embeddings - Loss: {loss_word2vec}')


### Prova

In [ ]:
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer

# Defineix funcions per calcular els embeddings de frases
def compute_mean_embedding(text, model, embedding_dim):
    """
    Agafa els vectors d'embeddings de cada paraula en una frase o document i 
    calcula la mitjana dels vectors per obtenir una única representació vectorial 
    per a la frase o document.
    """
    vectors = [model[word] for word in text if word in model]
    if vectors:
        mean_vector = np.mean(vectors, axis=0)
    else:
        mean_vector = np.zeros(embedding_dim)
    return mean_vector

def compute_weighted_mean_embedding(text, model, word2tfidf, embedding_dim):
    """
    Utilitza una ponderació per a cada vector de paraula, com ara la freqüència 
    inversa del document (TF-IDF), per calcular una mitjana ponderada dels vectors.
    """
    vectors = [model[word] * word2tfidf[word] for word in text if word in model and word in word2tfidf]
    if vectors:
        weighted_mean_vector = np.mean(vectors, axis=0)
    else:
        weighted_mean_vector = np.zeros(embedding_dim)
    return weighted_mean_vector

In [ ]:
# Exemple de corpus
corpus = ["Aquest és un text de exemple", "Aquí hi ha un altre text"]

# Prepara els vectors TF-IDF
tfidf = TfidfVectorizer()
tfidf_matrix = tfidf.fit_transform(corpus)
word2tfidf = dict(zip(tfidf.get_feature_names_out(), tfidf.idf_))

In [ ]:
# Exemple d'ús amb embeddings pre-entrenats (Word2Vec)
from gensim.models import KeyedVectors
import tensorflow as tf

# Carrega el model pre-entrenat (substitueix 'path_to_model' amb la ruta real)
# word2vec_model = KeyedVectors.load_word2vec_format('path_to_model', binary=True)

# Defineix la longitud de les seqüències i la dimensió dels embeddings
input_length = 10
embedding_dim = model_100MB.vector_size

# Prepara les dades d'entrenament
X_train1 = np.array([compute_mean_embedding(text.split(), model_100MB.wv, embedding_dim) for text in corpus])
X_train2 = np.array([compute_weighted_mean_embedding(text.split(), model_100MB.wv, word2tfidf, embedding_dim) for text in corpus])
y_train = np.random.rand(len(corpus), 1)

# Defineix el model de Keras (ajusta les dimensions segons la longitud de les seqüències i la dimensió dels embeddings)
def build_and_compile_model(input_dim, hidden_size=64):
    input_1 = tf.keras.Input(shape=(input_dim,))
    input_2 = tf.keras.Input(shape=(input_dim,))
    
    concatenate = tf.keras.layers.Concatenate(axis=-1)([input_1, input_2])
    hidden = tf.keras.layers.Dense(hidden_size, activation='relu')(concatenate)
    output = tf.keras.layers.Dense(1)(hidden)
    
    model = tf.keras.Model(inputs=[input_1, input_2], outputs=output)
    model.compile(loss='mean_absolute_error', optimizer=tf.keras.optimizers.Adam(0.001))
    
    return model

# Construir i compilar el model
m = build_and_compile_model(input_dim=embedding_dim)

# Entrenar el model
m.fit([X_train1, X_train2], y_train, epochs=10, batch_size=32)

# Exemple de predicció
input_data1 = compute_mean_embedding("Aquest és un text de exemple".split(), model_100MB.wv, embedding_dim).reshape(1, -1)
input_data2 = compute_weighted_mean_embedding("Aquí hi ha un altre text".split(), model_100MB.wv, word2tfidf, embedding_dim).reshape(1, -1)

# Predir la similitud
y_pred = m.predict([input_data1, input_data2])
print(y_pred)

Epoch 1/10
1/1 [==============================] - 0s 334ms/step - loss: 0.7557
Epoch 2/10
1/1 [==============================] - 0s 3ms/step - loss: 0.1112
Epoch 3/10
1/1 [==============================] - 0s 2ms/step - loss: 0.4268
Epoch 4/10
1/1 [==============================] - 0s 5ms/step - loss: 0.5486
Epoch 5/10
1/1 [==============================] - 0s 3ms/step - loss: 0.4800
Epoch 6/10
1/1 [==============================] - 0s 5ms/step - loss: 0.3008
Epoch 7/10
1/1 [==============================] - 0s 3ms/step - loss: 0.0543
Epoch 8/10
1/1 [==============================] - 0s 4ms/step - loss: 0.2087
Epoch 9/10
1/1 [==============================] - 0s 2ms/step - loss: 0.2880
Epoch 10/10
1/1 [==============================] - 0s 55ms/step
[[0.10263795]]


In [ ]:
y_train

array([[0.24829134],
       [0.49559584]])